# Sentiment Analysis on Spanish IMDb reviews using a Ruperta model
## Steps to finetune a Hugginface model on SageMaker, make batch predictions and upload the model to the Hub

1. [Introduction](#Introduction)  
    1. [The Problem](#The-Problem)
    2. [The Dataset](#The-Dataset)
2. [Setting up the Environment](#Setting-up-the-Environment)
    1. [Installation](#Installation)  
    2. [Define global variables and parameters](#Define-global-variables-and-parameters)  
    3. [Create the SageMaker Session](#Create-the-SageMaker-Session)
3. [Processing](#Preprocessing)   
    1. [Tokenization](#Tokenization)  
    2. [Uploading data to sagemaker_session_bucket](#Uploading-data-to-sagemaker_session_bucket)  
4. [Fine-tuning & starting Sagemaker Training Job](#Fine-tuning-\&-starting-Sagemaker-Training-Job)  
    1. [Creating an Estimator and start a training job](#Creating-an-Estimator-and-start-a-training-job)  
    2. [Estimator Parameters](#Estimator-Parameters)   
    3. [Download fine-tuned model from s3](#Download-fine-tuned-model-from-s3)
    3. [Attach to old training job to an estimator ](#Attach-to-old-training-job-to-an-estimator)  
5. [_Coming soon_:Push model to the Hugging Face hub](#Push-model-to-the-Hugging-Face-hub)

# Introduction

On March 2021, Amazon AWS and Huggingface release a new SageMaker estimator optimized to work with Huggingface models, so you do not need to create a custom container. From that moment on, working with transformers library is much easier and more agile in the SageMaker environment.

In this notebook, we will describe the most relevant steps to train a Hugginface model in AWS SageMaker using the Huggingface estimators, showing how to deal with sagemaker experiments and how to make predictions with a Batch Transform job. Finally, we will upload the new model to the Huggingface Hub. Some basic concepts on SageMaker will not be detailed in order to focus on the relevant concepts

The following steps will be explained: 
 
1. Create an Experiment and Trial to keep track of our experiments
2. Load the training data to our training instance and create the train, validation, and test datasets and upload them to S3
3. Create the scripts to train our Huggingface model, a RoBERTa based model pretrained in a Spanish corpus: RuPERTa.
4. Create an Estimator to train our model in a huggingface container in script mode
5. Download and deploy the trained model to make predictions
6. Create a Batch Transform job to make predictions for the test dataset 
7. Upload the trained model to the Huggingface Hub

Some sections of this notebook has been inspired by the tutorial on Huggingface doc:
https://github.com/huggingface/notebooks/blob/master/sagemaker/01_getting_started_pytorch/sagemaker-notebook.ipynb

## The Problem

We will describe how to finetune a binary Text-Classifier or a Sentiment Analyzer using a dataset in Spanish. Many of the published models have been trained on English texts, but in this project, we want to work with a Spanish dataset and a Spanish pretrained RoBERTa model called RuPERTa:

*"RuPERTa-base (uncased) is a RoBERTa model trained on an uncased version of big Spanish corpus. RoBERTa iterates on BERT's pretraining procedure, including training the model longer, with bigger batches over more data; removing the next sentence prediction objective; training on longer sequences; and dynamically changing the masking pattern applied to the training data. The architecture is the same as roberta-base"* by Manuel Romero (https://huggingface.co/mrm8488)

## The Dataset

In particular, the pre-trained model will be finetuned using a dataset of IMDB reviews in spanish.The dataset is a collection of movie reviews in Spanish, about 50,000 reviews. The dataset is balanced and provides every review in english, in spanish and the label in both languages.

Sizes of datasets:

- Train dataset: 42,500
- Validation dataset: 3,750
- Test dataset: 3,750


# Setting up the environment

## Installation

We will install the transformers, datasets and sagemaker library:

In [1]:
#!pip install "sagemaker>=2.48.0" "transformers==4.12.1" "datasets[s3]==1.6.2" --upgrade
#!pip install "sagemaker>=2.48.0" "transformers==4.12.3" "datasets==1.13" --upgrade
!pip install "sagemaker>=2.48.0" "transformers==4.12.3" "datasets" --upgrade

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
     |████████████████████████████████| 473 kB 25.5 MB/s            
  Preparing metadata (setup.py) ... done
     |████████████████████████████████| 3.1 MB 106.1 MB/s            
     |████████████████████████████████| 306 kB 103.5 MB/s            
     |████████████████████████████████| 895 kB 110.0 MB/s            
     |████████████████████████████████| 3.3 MB 100.3 MB/s            
     |████████████████████████████████| 61 kB 1.3 MB/s              
     |████████████████████████████████| 76 kB 859 kB/s              
     |████████████████████████████████| 243 kB 105.6 MB/s            
     |████████████████████████████████| 132 kB 114.5 MB/s            


  Created wheel for sagemaker: filename=sagemaker-2.72.1-py2.py3-none-any.whl size=650653 sha256=51b4f16f2ed313db6a0329c66e3365849f54de8b7aa8dc751c37a266ebef832a
  Stored in directory: /home/ec2-user/.cache/pip/wheels/2d/2f/42/cb1762fdbe69d2b678e36c3b81e9f6fa2c03b08d5de5471edd
Successfully built sagemaker
  Attempting uninstall: tqdm
    Found existing installation: tqdm 4.62.0
    Uninstalling tqdm-4.62.0:
      Successfully uninstalled tqdm-4.62.0
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2021.4.0
    Uninstalling fsspec-2021.4.0:
      Successfully uninstalled fsspec-2021.4.0
  Attempting uninstall: sagemaker
    Found existing installation: sagemaker 2.70.0
    Uninstalling sagemaker-2.70.0:
      Successfully uninstalled sagemaker-2.70.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
spacy 3.2.0 requires typing-extensions<4.0.

In [1]:
#!pip install "sagemaker>=2.69.0" "transformers==4.12.3" --upgrade
# using older dataset due to incompatibility of sagemaker notebook & aws-cli with > s3fs and fsspec to >= 2021.10
#!pip install  "datasets==1.13" --upgrade

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
     |████████████████████████████████| 3.1 MB 32.2 MB/s            
     |████████████████████████████████| 895 kB 129.8 MB/s            
     |████████████████████████████████| 59 kB 21.6 MB/s             
     |████████████████████████████████| 3.3 MB 114.9 MB/s            
Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
     |████████████████████████████████| 285 kB 41.2 MB/s            
     |████████████████████████████████| 243 kB 130.7 MB/s            


     |████████████████████████████████| 56 kB 13.7 MB/s             
     |████████████████████████████████| 76 kB 14.0 MB/s             
     |████████████████████████████████| 132 kB 138.1 MB/s            
  Attempting uninstall: tqdm
    Found existing installation: tqdm 4.62.0
    Uninstalling tqdm-4.62.0:
      Successfully uninstalled tqdm-4.62.0
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2021.4.0
    Uninstalling fsspec-2021.4.0:
      Successfully uninstalled fsspec-2021.4.0
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 0.1.2
    Uninstalling huggingface-hub-0.1.2:
      Successfully uninstalled huggingface-hub-0.1.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
transformers 4.12.3 requires huggingface-hub<1.0,>=0.1.0, but you have huggingface-hub 0.0.19 which is incompatible.
s3fs

## Loading the libraries

Let's start by loading some libraries:

In [2]:
import sagemaker
print(sagemaker.__version__)

2.68.0


In [3]:
import pandas as pd
import os
import time

## Define global variables and parameters

Setting the variables for the pretrained model to use:

In [4]:
# tokenizer used in preprocessing
# Define the base model  name  we will fine-tune
#model_name = "mrm8488/RuPERTa-base"
model_name = "dccuchile/bert-base-spanish-wwm-cased"

# tokenizer used in preprocessing
#tokenizer_name = "mrm8488/RuPERTa-base"
tokenizer_name = model_name
# Define my trained final model name
#mymodel_name='RuPERTa_base_sentiment_analysis_es'
mymodel_name='BETO_base_sentiment_analysis_es'


The next section defines the data location variables:

In [5]:
# Set the variables for data locations
data_folder_name='data'
data_filename = 'IMDB Dataset SPANISH.csv'

# Set the absolute path of the train data 
train_file = os.path.abspath(os.path.join(data_folder_name, data_filename))
# Specify your bucket name
bucket_name = 'edumunozsala-ml-sagemaker'
# Set the training data folder in S3
training_folder = r'ruperta-sentiment/train'
# Set the training data folder in S3
val_folder = r'ruperta-sentiment/validation'
# Set the training data folder in S3
test_folder = r'ruperta-sentiment/test'
# Set the output folder in S3
#output_folder = r'ruperta-sentiment'
output_folder = mymodel_name
# Set the checkpoint in S3 folder for our model 
#ckpt_folder = r'ruperta-sentiment/ckpt'
ckpt_folder = mymodel_name+ '/ckpt'
# Set variables for S3 folders
training_data_uri = r's3://' + bucket_name + r'/' + training_folder
val_data_uri = r's3://' + bucket_name + r'/' + val_folder
test_data_uri = r's3://' + bucket_name + r'/' + test_folder
output_data_uri = r's3://' + bucket_name + r'/' + output_folder
ckpt_data_uri = r's3://' + bucket_name + r'/' + ckpt_folder

# To limit the number of data examples, for rapid testing
#nrows=

## Create the SageMaker Session 

_If you are going to use Sagemaker in a local environment. You need access to an IAM Role with the required permissions for Sagemaker. You can find [here](https://docs.aws.amazon.com/sagemaker/latest/dg/sagemaker-roles.html) more about it._

In [6]:
import sagemaker

sess = sagemaker.Session()
# sagemaker session bucket -> used for uploading data, models and logs
# sagemaker will automatically create this bucket if it not exists
# Specify your bucket name
sagemaker_session_bucket= bucket_name
if sagemaker_session_bucket is None and sess is not None:
    # set to default bucket if a bucket name is not given
    sagemaker_session_bucket = sess.default_bucket()

role = sagemaker.get_execution_role()
sess = sagemaker.Session(default_bucket=sagemaker_session_bucket)
region = sess.boto_session.region_name

print(f"sagemaker role arn: {role}")
print(f"sagemaker bucket: {sess.default_bucket()}")
print(f"sagemaker session region: {sess.boto_region_name}")

sagemaker role arn: arn:aws:iam::223817798831:role/workshop-sagemaker-kfp-role
sagemaker bucket: edumunozsala-ml-sagemaker
sagemaker session region: us-east-1


## Preprocessing and splitting the datasets

We are using a dataset of IMDB reviews in spanish. After preprocessing, the dataset will be uploaded to our `sagemaker_session_bucket` to be used within our training job. First we load the dataset from a CSV file:

In [12]:
# Load the dataset from a CSV file
df=pd.read_csv(train_file, header=0, usecols=[2,4]) #, nrows=10000)
print('Num Examples: ',len(df))
# Check for null values
print('Null Values\n', df.isna().sum())
print(df.head(5))

Num Examples:  50000
Null Values
 review_es      0
sentimiento    0
dtype: int64
                                           review_es sentimiento
0  Uno de los otros críticos ha mencionado que de...    positivo
1  Una pequeña pequeña producción.La técnica de f...    positivo
2  Pensé que esta era una manera maravillosa de p...    positivo
3  Básicamente, hay una familia donde un niño peq...    negativo
4  El "amor en el tiempo" de Petter Mattei es una...    positivo


Transform the target column to integer values, 1 for positive and 0 for negative:

In [13]:
#Create a dictonary to map the sentiment value to a integer value
sentiments = {"positivo":1, "negativo":0}
df['sentimiento'] = df['sentimiento'].map(sentiments)
# Show the results
print(df.head(5))

                                           review_es  sentimiento
0  Uno de los otros críticos ha mencionado que de...            1
1  Una pequeña pequeña producción.La técnica de f...            1
2  Pensé que esta era una manera maravillosa de p...            1
3  Básicamente, hay una familia donde un niño peq...            0
4  El "amor en el tiempo" de Petter Mattei es una...            1


Check the target value distribution to identify unbalanced classes:

In [14]:
#Check value counts for the target column
print(df['sentimiento'].value_counts())
#Check the maximum length of our text feature
print('Max length: ',max(df.review_es.apply(len)))

1    25000
0    25000
Name: sentimiento, dtype: int64
Max length:  13465


Both classes, Positive and Negative, are balanced. Fine!!

## Split the data into train and validation dataset

We split the dataset into a training dataset (90%) and a validation dataset (10%). To choose the examples, there is a sampling method to randomly extract the training dataset.

In [15]:
from sklearn.model_selection import train_test_split

# Define our text and label arrays
train_texts = df['review_es'].tolist()
train_labels = df['sentimiento'].tolist()

# Splitting the data into training, validation and test data
# Split the train data, containing 80%
train_texts, val_texts, train_labels, val_labels = train_test_split(train_texts, train_labels, test_size=.15) #.15 full training
# split the validation and test data
val_texts, test_texts, val_labels, test_labels = train_test_split(val_texts, val_labels, test_size=.5) #.5 full training

print('Length Train dataset: ', len(train_texts))
print('Length Val dataset: ', len(val_texts))
print('Length test dataset: ', len(test_texts))

Length Train dataset:  42500
Length Val dataset:  3750
Length test dataset:  3750


In [16]:
print('Length Train dataset: ', len(train_texts))
print('Length Val dataset: ', len(val_texts))
print('Length test dataset: ', len(test_texts))

Length Train dataset:  42500
Length Val dataset:  3750
Length test dataset:  3750


In the next section, we try to limit the number of examples to train on in order to reduce the cost and time for training during the experiments. When the model is ready to be trained, we must train on the whole training dataset.

In [13]:
# RUN THIS CELL only IF YOU WANT TO LIMIT THE EXAMPLES TO REDUCE TRAINING TIME
# To limit the training and validation dataset, for testing
#max_train=256
max_val=64
#train_texts = train_texts[:max_train]
#train_labels = train_labels[:max_train]
val_texts = test_texts[:512]
val_labels = test_labels[:512]
print('Length Train dataset: ', len(train_texts))
print('Length test dataset: ', len(val_texts),len(val_labels),)
print(type(train_texts))

Length Train dataset:  12500
Length test dataset:  512 512
<class 'list'>


# Create an experiment and trial

*Amazon SageMaker Experiments* is a capability of Amazon SageMaker that lets you organize, track, compare, and evaluate your machine learning experiments.

Machine learning is an iterative process. You need to experiment with multiple combinations of data, algorithm and parameters, all the while observing the impact of incremental changes on model accuracy. Over time this iterative experimentation can result in thousands of model training runs and model versions. This makes it hard to track the best performing models and their input configurations. It’s also difficult to compare active experiments with past experiments to identify opportunities for further incremental improvements.

Experiments will help us to organize and manage all executions, metrics and results of a ML project.

In [7]:
# Install the library necessary to handle experiments
!pip install sagemaker-experiments

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
  Using cached sagemaker_experiments-0.1.35-py3-none-any.whl (42 kB)


Load the libraries to handle experiments

In [8]:
# Import the libraries to work with Experiments in SageMaker
from smexperiments.experiment import Experiment
from smexperiments.trial import Trial
from smexperiments.trial_component import TrialComponent
from smexperiments.tracker import Tracker

Set the experiment and trial name and one tag to help us to identify the reason for this items.

In [9]:
# Set the experiment name
experiment_name='ruperta-sentiment-analysis'
# Set the trial name 
trial_name = "{}-{}-{}".format(experiment_name,'beto-p2',time.strftime("%Y-%m-%d-%H-%M-%S", time.gmtime()))

tags = [{'Key': 'my-experiments', 'Value': 'rupertaSentAnalysis'}]

## Concepts

- Experiment: A collection of related Trials. Add Trials to an Experiment that you wish to compare together.
- Trial: A description of a multi-step machine learning workflow. Each step in the workflow is described by a Trial Component. There is no relationship between Trial Components such as ordering.
- Trial Component: A description of a single step in a machine learning workflow. For example data cleaning, feature extraction, model training, model evaluation, etc...
- Tracker: A Python context-manager for logging information about a single TrialComponent.

For more information see Amazon SageMaker Experiments - Organize, Track, and Compare Your Machine Learning Trainings

You can create an experiment to track all the model training iterations. Experiments are a great way to organize your data science work. You can create experiments to organize all your model development work for : a business use case you are addressing (e.g. create experiment named “customer churn prediction”), or a data science team that owns the experiment (e.g. create experiment named “marketing analytics experiment”), or a specific data science and ML project. Think of it as a “folder” for organizing your “files”.

We will create a Trial to track each training job run. But this is just a simple example, not intented to explore all the capabilities of the product.

In [10]:
# create the experiment if it doesn't exist
try:
    training_experiment = Experiment.load(experiment_name=experiment_name)
    print('Loaded experiment ',experiment_name)
except Exception as ex:
    if "ResourceNotFound" in str(ex):
        training_experiment = Experiment.create(experiment_name=experiment_name,
                                      description = "Experiment to track trainings on a ruperta Sentiment Analyzer", 
                                      tags = tags)
        print('Created experiment ',experiment_name)
# create the trial if it doesn't exist
try:
    single_gpu_trial = Trial.load(trial_name=trial_name)
    print('Loaded trial ',trial_name)
except Exception as ex:
    if "ResourceNotFound" in str(ex):
        single_gpu_trial = Trial.create(experiment_name=experiment_name, 
                             trial_name= trial_name,
                             tags = tags)
        print('Created trial ',trial_name)

Loaded experiment  ruperta-sentiment-analysis
Created trial  ruperta-sentiment-analysis-beto-p2-2021-12-24-11-53-44


## Setting the model and training parameters

Now it is time to set the model and training parameters, they will be passed to the dataset generator and to the estimator object in a latter section.

In [11]:
TRAIN_BATCH_SIZE = 32   # input batch size for training (default: 64)
VALID_BATCH_SIZE = 8    # input batch size for testing (default: 1000)
TRAIN_EPOCHS = 5       # number of epochs to train (default: 10)
LEARNING_RATE = 3e-5    # learning rate (default: 0.01)
SEED = 42               # random seed (default: 42)
MAX_LEN = 256           # Max length for product description

## Tokenization

The preprocessing step includes the tokenization of our datasets. In this exercise, we are not going to apply any other action to our input data.    

Load the tokenizer:

In [17]:
from datasets import load_dataset
from transformers import AutoTokenizer

# Loading the RoBERTa Tokenizer
tokenizer = AutoTokenizer.from_pretrained(tokenizer_name, do_lower_case=False)
# checking the loaded tokenizer
print(tokenizer.bos_token)
print(tokenizer.eos_token)

INFO:filelock:Lock 140393757762000 acquired on /home/ec2-user/.cache/huggingface/transformers/ca34e6c1251888a8ed98da2a454f869d28e3438eef67c2f93aa8133459ac08a3.0e90f656d0426b15b4927d1fe8ca5ec4c2e7b0d0e878c9153c3ddc6ed9bbed3c.lock


Downloading:   0%|          | 0.00/364 [00:00<?, ?B/s]

INFO:filelock:Lock 140393757762000 released on /home/ec2-user/.cache/huggingface/transformers/ca34e6c1251888a8ed98da2a454f869d28e3438eef67c2f93aa8133459ac08a3.0e90f656d0426b15b4927d1fe8ca5ec4c2e7b0d0e878c9153c3ddc6ed9bbed3c.lock
INFO:filelock:Lock 140393769527696 acquired on /home/ec2-user/.cache/huggingface/transformers/cb7cedb04246e225d56ba26d207f1d1809b31a9bbe9b63103371d835c6ac0502.f4e4777229bac528fa2a8d4833e2ef53624e985ebde0fd527064a5cc7c50832b.lock


Downloading:   0%|          | 0.00/648 [00:00<?, ?B/s]

INFO:filelock:Lock 140393769527696 released on /home/ec2-user/.cache/huggingface/transformers/cb7cedb04246e225d56ba26d207f1d1809b31a9bbe9b63103371d835c6ac0502.f4e4777229bac528fa2a8d4833e2ef53624e985ebde0fd527064a5cc7c50832b.lock
INFO:filelock:Lock 140393757884496 acquired on /home/ec2-user/.cache/huggingface/transformers/6761cd0c3d282272f598fcc1fa8c4ecfff8c18762ec8acb40f9cbb562cb0901e.6587bde86239957281af55b2f7e564df111a2b4f9dfc0ad884f13ea7106e4dfb.lock


...

Downloading:   0%|          | 0.00/469k [00:00<?, ?B/s]

INFO:filelock:Lock 140393757977936 released on /home/ec2-user/.cache/huggingface/transformers/44de7af89c157bf67367a71105165d92bebe0585543739a918e3870d25484c27.6a099cd4b12bf7db174fffe48b004eb919c325f108e0c36176a0fe0ad1848d31.lock
INFO:filelock:Lock 140393757888208 acquired on /home/ec2-user/.cache/huggingface/transformers/9848a00af462c42dfb4ec88ef438fbab5256330f7f6f50badc48d277f9367d49.f982506b52498d4adb4bd491f593dc92b2ef6be61bfdbe9d30f53f963f9f5b66.lock


Downloading:   0%|          | 0.00/134 [00:00<?, ?B/s]

INFO:filelock:Lock 140393757888208 released on /home/ec2-user/.cache/huggingface/transformers/9848a00af462c42dfb4ec88ef438fbab5256330f7f6f50badc48d277f9367d49.f982506b52498d4adb4bd491f593dc92b2ef6be61bfdbe9d30f53f963f9f5b66.lock
Using bos_token, but it is not set yet.
Using eos_token, but it is not set yet.


None
None


## Prepare and create the dataset

Now we can simply pass our texts to the tokenizer. We’ll pass `truncation=True` and `padding=True`, which will ensure that all of our sequences are padded to the same length and are truncated to be no longer than the max length. This will allow us to feed batches of sequences into the model at the same time.

In [18]:
# Tokenize the train and test data
train_encodings = tokenizer(train_texts, truncation=True, padding=True, max_length=MAX_LEN) # max_length
val_encodings = tokenizer(val_texts, truncation=True, padding=True, max_length=MAX_LEN) # max_length


Now, let’s turn our labels and encodings into a Dataset object. In PyTorch, this is done by subclassing a torch.utils.data.Dataset object and implementing the __len__ and __getitem__ functions. 

In [19]:
import torch

class IMDbReviews(torch.utils.data.Dataset):
  ''' Dataset for our IMDb revies in spanish 
  '''

  def __init__(self, encodings, labels):
      self.encodings = encodings
      self.labels = labels

  def __getitem__(self, idx):
      item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
      item['labels'] = torch.tensor(self.labels[idx])
      return item

  def __len__(self):
      return len(self.labels)

# Create the train dataset
train_dataset = IMDbReviews(train_encodings, train_labels)
# Create the vsalidation dataset
val_dataset = IMDbReviews(val_encodings, val_labels)

In [ ]:
# load dataset
#train_dataset, test_dataset = load_dataset('imdb', split=['train', 'test'])
#test_dataset = test_dataset.shuffle().select(range(10000)) # smaller the size for test dataset to 10k 
'''
# tokenize dataset
train_dataset = train_dataset.map(tokenize, batched=True)
test_dataset = test_dataset.map(tokenize, batched=True)

# set format for pytorch
train_dataset =  train_dataset.rename_column("label", "labels")
train_dataset.set_format('torch', columns=['input_ids', 'attention_mask', 'labels'])
test_dataset = test_dataset.rename_column("label", "labels")
test_dataset.set_format('torch', columns=['input_ids', 'attention_mask', 'labels'])
'''

## Uploading data to S3 `sagemaker_session_bucket`

After we processed the `datasets`, we need to save them to disk and then we will upload our datasets to S3.

In [20]:
import botocore
# save train_dataset to disk
train_filename = os.path.abspath(os.path.join(data_folder_name, 'train_data.pt'))
print('Train Datafile: ',train_filename)
torch.save(train_dataset, train_filename)

# save test_dataset to disk
val_filename = os.path.abspath(os.path.join(data_folder_name, 'val_data.pt'))
print('Validation Datafile: ',val_filename)
torch.save(val_dataset, val_filename)

Train Datafile:  /home/ec2-user/SageMaker/ruperta_sentiment_analysis/data/train_data.pt
Validation Datafile:  /home/ec2-user/SageMaker/ruperta_sentiment_analysis/data/val_data.pt


As we are going to test our model lately using the model deployed, we have to save the test dataset in text format, not tokenized.

**Important: Text inputs to the model must be truncated to the max length of the model**

In [21]:
import json

# Save the test dataset to jsonl file
test_filename = os.path.abspath(os.path.join(data_folder_name, 'test_data.jsonl'))

with open(test_filename, "w+") as outfile:
    for text in test_texts:
        # Create a Dict with 'input' as key and the text as value
        row = {'inputs': text[:MAX_LEN]}
        # Write the dict to the output file 
        json.dump(row, outfile)
        # Add an endline
        outfile.write('\n')


We also have to save the test labels to compare results when evaluating the model performance:

In [22]:
# Save the test dataset to jsonl file
test_labels_filename = os.path.abspath(os.path.join(data_folder_name, 'test_labels.jsonl'))

with open(test_labels_filename, "w+") as outfile:
    for label in test_labels:
        # Create a Dict with 'input' as key and the text as value
        row = {'labels': label}
        # Write the dict to the output file 
        json.dump(row, outfile)
        # Add an endline
        outfile.write('\n')


## Upload the datasets to S3 filesystem
Then we can upload to the training, validation and test data folders in S3 the files necessary for training and evaluation. Once uploaded they can be loaded for training in the SageMaker container.

In [23]:
train_data_input = sess.upload_data(train_filename,
                              bucket=sagemaker_session_bucket, 
                              key_prefix=training_folder)

val_data_input = sess.upload_data(val_filename,
                              bucket=sagemaker_session_bucket, 
                              key_prefix=val_folder)

test_data_input = sess.upload_data(test_filename,
                              bucket=sagemaker_session_bucket, 
                              key_prefix=test_folder)

print(train_data_input)
print(val_data_input)
print(test_data_input)

s3://edumunozsala-ml-sagemaker/ruperta-sentiment/train/train_data.pt
s3://edumunozsala-ml-sagemaker/ruperta-sentiment/validation/val_data.pt
s3://edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl


# Fine-tuning & starting Sagemaker Training Job

In order to create a sagemaker training job we need an `HuggingFace` Estimator. The Estimator handles end-to-end Amazon SageMaker training and deployment tasks. In a Estimator we define, which fine-tuning script should be used as `entry_point`, which `instance_type` should be used, which `hyperparameters` are passed in .....



```python
huggingface_estimator = HuggingFace(entry_point='train.py',
                            source_dir='./scripts',
                            base_job_name='huggingface-sdk-extension',
                            instance_type='ml.p3.2xlarge',
                            instance_count=1,
                            transformers_version='4.4',
                            pytorch_version='1.6',
                            py_version='py36',
                            role=role,
                            hyperparameters = {'epochs': 1,
                                               'train_batch_size': 32,
                                               'model_name':'distilbert-base-uncased'
                                                })
```

When we create a SageMaker training job, SageMaker takes care of starting and managing all the required ec2 instances for us with the `huggingface` container, uploads the provided fine-tuning script `train.py` and downloads the data from our `sagemaker_session_bucket` into the container at `/opt/ml/input/data`. Then, it starts the training job by running. 

```python
/opt/conda/bin/python train.py --epochs 1 --model_name distilbert-base-uncased --train_batch_size 32
```

The `hyperparameters` you define in the `HuggingFace` estimator are passed in as named arguments. 

Sagemaker is providing useful properties about the training environment through various environment variables, including the following:

* `SM_MODEL_DIR`: A string that represents the path where the training job writes the model artifacts to. After training, artifacts in this directory are uploaded to S3 for model hosting.

* `SM_NUM_GPUS`: An integer representing the number of GPUs available to the host.

* `SM_CHANNEL_XXXX:` A string that represents the path to the directory that contains the input data for the specified channel. For example, if you specify two input channels in the HuggingFace estimator’s fit call, named `train` and `test`, the environment variables `SM_CHANNEL_TRAIN` and `SM_CHANNEL_TEST` are set.


To run your training job locally you can define `instance_type='local'` or `instance_type='local_gpu'` for gpu usage. _Note: this does not working within SageMaker Studio_


In [ ]:
!pygmentize ./scripts/train.py

## Define the training hyperparameters 

In [ ]:
#!pip install sagemaker --upgrade

Let's create a dictionary containing the hyperparameters for our training job:


In [24]:
from sagemaker.huggingface import HuggingFace

# Set the model name to fine tune
# model_name = "mrm8488/RuPERTa-base"

# hyperparameters, which are passed into the training job
hyperparameters={'epochs': TRAIN_EPOCHS, #TRAIN_EPOCHS,
                 'train_batch_size': TRAIN_BATCH_SIZE,
                 'eval_batch_size': VALID_BATCH_SIZE,
                 'model_name': model_name, #pretrained model
                 'train_filename': 'train_data.pt',
                 'val_filename': 'val_data.pt',
                 # Uncomment when resuming 
                 #'checkpoint': 'checkpoint-',
                 'learning_rate': LEARNING_RATE,                          # learning rate used during training
                 'fp16': True,                                   # Whether to use 16-bit (mixed) precision training                 
                 }

## Create a huggingface Estimator

To keep track of the training process, we assign the trail name to our training job and then we can create the `estimator` for our Huggingface model.

In [25]:
# Set the job name and show it
#job_name = '{}-{}'.format(trial_name,time.strftime("%Y-%m-%d-%H-%M-%S", time.gmtime()))
#job_name = '{}-{}'.format(trial_name,time.strftime("%H-%M", time.gmtime()))
job_name= trial_name
print(job_name)

ruperta-sentiment-analysis-beto-p2-2021-12-24-11-53-44


In [28]:
huggingface_estimator = HuggingFace(entry_point='train.py',
                            source_dir='./scripts',
                            instance_type='ml.p2.xlarge',
                            #instance_type='local',
                            instance_count=1,
                            role=role,
                            output_path=output_data_uri,
                            code_location=output_data_uri,
                            checkpoint_s3_uri = ckpt_data_uri, #output_data_uri,
                            transformers_version='4.6',
                            pytorch_version='1.7',
                            py_version='py36',
                            hyperparameters = hyperparameters)

## Create a Tracker

Another interesting tool to mention, is Tracker objects. They can store information about different types of topics or objects in our model or training process like inputs, parameters, artifacts or metrics. The tracker is attached to a trial, associating the object to the training job. We can record that information and analyze it later on the experiment. **Note** that only parameters, input artifacts, and output artifacts are saved to SageMaker. Metrics are saved to file.

As an example, we create a Tracker to register the input data and two parameters about how that data is processed in our project.

In [29]:
# Create the tracker for the inout data
tracker_name='Training'
trial_comp_name = None # Change to a an exsting TrialComponent to load it

try:
    tracker = Tracker.load(trial_component_name=trial_comp_name)
    print('Loaded Tracker ',tracker_name)
except Exception as ex:
    tracker = Tracker.create(display_name=tracker_name)
    # Register the training dataset
    tracker.log_input(name="train-data-imdb-reviews-es", media_type="s3/uri", value=train_data_input)
    # Register the validation dataset
    tracker.log_input(name="val-data-imdb-reviews-es", media_type="s3/uri", value=val_data_input)
    # Register the output model dir
    tracker.log_output(name="model_dir", media_type="s3/uri", value=output_data_uri)
    
    # Track the hyperpatameters
    tracker.log_parameters(hyperparameters)
    
    print('Created Tracker ',tracker_name)
    
# Atach the Tracker to the trial
single_gpu_trial.add_trial_component(tracker.trial_component)

Created Tracker  Training


Our last step consist in create the experiment configuration, a dictionary that contains the experiment name, the trial name and the trial component and it will be used to label our training job.

In [30]:
# Create a configuration definition for our experiment and trial
trial_comp_name = 'training-component'
# Set the configuration parameters for the experiment
experiment_config = {'ExperimentName': training_experiment.experiment_name, 
                       'TrialName': single_gpu_trial.trial_name,
                       'TrialComponentDisplayName': trial_comp_name}

Check and show information about the experiment and trial

In [31]:
print('Experiment: ',training_experiment.experiment_name)
# Show the trials in the experiment
#for trial in training_experiment.list_trials():
    #print('Trial: ',trial.trial_name)

for trial_comp in TrialComponent.list(trial_name=single_gpu_trial.trial_name):
        print('Trial Components: ',trial_comp)

Experiment:  ruperta-sentiment-analysis
Trial Components:  TrialComponentSummary(trial_component_name='TrialComponent-2021-12-24-121230-aoge',trial_component_arn='arn:aws:sagemaker:us-east-1:223817798831:experiment-trial-component/trialcomponent-2021-12-24-121230-aoge',display_name='Training',creation_time=datetime.datetime(2021, 12, 24, 12, 12, 30, 988000, tzinfo=tzlocal()),created_by={},last_modified_time=datetime.datetime(2021, 12, 24, 12, 12, 30, 988000, tzinfo=tzlocal()),last_modified_by={})


## Calling fit to train the model with a Huggingface container.

Now it is time to train our model, we just need to call the `fit` method passing the input data channels and the experiment configuration. For our example, **the training job will last about 10 hours** and we are not going to wait for te training job to finish.

In [32]:
# starting the train job with our uploaded datasets as input
huggingface_estimator.fit({'train': training_data_uri, 'validation': val_data_uri}, job_name = job_name, 
              experiment_config = experiment_config, wait=False)


INFO:sagemaker.image_uris:Defaulting to the only supported framework/algorithm version: latest.
INFO:sagemaker.image_uris:Ignoring unnecessary instance type: None.
INFO:sagemaker:Creating training-job with name: ruperta-sentiment-analysis-beto-p2-2021-12-24-11-53-44


Save the experiment, then you can view it and its trials from SageMaker Studio

In [44]:
# Save the trial
single_gpu_trial.save()
# Save the experiment
training_experiment.save()

Experiment(sagemaker_boto_client=<botocore.client.SageMaker object at 0x7f1da7269f10>,experiment_name='ruperta-sentiment-analysis',experiment_arn='arn:aws:sagemaker:us-east-1:223817798831:experiment/ruperta-sentiment-analysis',display_name='ruperta-sentiment-analysis',description='Experiment to track trainings on a ruperta Sentiment Analyzer',creation_time=datetime.datetime(2021, 12, 5, 18, 44, 29, 398000, tzinfo=tzlocal()),created_by={},last_modified_time=datetime.datetime(2021, 12, 6, 18, 13, 47, 689000, tzinfo=tzlocal()),last_modified_by={},response_metadata={'RequestId': 'ce88e2b2-4a14-4708-971f-ae660af3bab1', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'ce88e2b2-4a14-4708-971f-ae660af3bab1', 'content-type': 'application/x-amz-json-1.1', 'content-length': '98', 'date': 'Mon, 06 Dec 2021 22:01:06 GMT'}, 'RetryAttempts': 0})

## Deploying the endpoint

To deploy our endpoint, we call `deploy()` on our HuggingFace estimator object, passing in our desired number of instances and instance type.

In [2]:
from sagemaker.huggingface import HuggingFace

#Set the S3 URI with the model data
# Check if the huggingface_estimator is defined, if not we restore the training job to our estimator variable
try:
    print('S3 Model dir: ',huggingface_estimator.model_data)
except:
    # Set the training job you want to attach to the estimator object
    # Use this option if the training job was not trained in this execution
    my_training_job_name = 'ruperta-sentiment-analysis-full-p2-2021-12-06-20-32-27'

    # Attach the estimator to the selected training job
    huggingface_estimator = HuggingFace.attach(my_training_job_name)
    print('Restored Huggingface estimator')

# Deploy the model on a m5 instance
predictor = huggingface_estimator.deploy(1,"ml.m5.xlarge")

S3 Model dir:  s3://edumunozsala-ml-sagemaker/ruperta-sentiment/ruperta-sentiment-analysis-full-p2-2021-12-06-20-32-27/output/model.tar.gz
-----!

Then, we use the returned predictor object to call the endpoint.

In [4]:
review = "Esta película fue excelente, un poco aterradora, pero excelente en eso.Para aquellos de ustedes que han oído hablar de Columbine y conocer la historia. Es en serio ese bien. Pero después de esta película creo que deberás tomar todo en serio.Algunas personas están locas y nunca sabes cuáles son, así que tómala en serio y no están bajo la estimación de alguien."

In [5]:
sentiment_input= {"inputs":review}

predictor.predict(sentiment_input)

[{'label': 'Positivo', 'score': 0.9989214539527893}]

Finally, we delete the endpoint again.

In [6]:
predictor.delete_endpoint()

# Run Batch Transform Inference Job with a fine-tuned model using jsonl

Batch transform is recommended when you need to do the following:

- Preprocess datasets to remove noise or bias that interferes with training or inference from your dataset.

- Get inferences from large datasets.

- Run inference when you don't need a persistent endpoint.

- Associate input records with inferences to assist the interpretation of results.


Example notebook: 

https://github.com/huggingface/notebooks/blob/master/sagemaker/12_batch_transform_inference/sagemaker-notebook.ipynb


### Data Pre-Processing

Data preprocessing was described and executed in a previous section when we built the datasets.

_NOTE: While preprocessing you need to make sure that your inputs fit the max_length.

## Create Inference Transformer to run the batch job

*When a batch transform job starts, SageMaker initializes compute instances and distributes the inference or preprocessing workload between them. Batch Transform partitions the Amazon S3 objects in the input by key and maps Amazon S3 objects to instances. When you have multiples files, one instance might process input1.csv, and another instance might process the file named input2.csv.*

SageMaker Documentation 

As we launch the training job ina previous session, we have to restore the `estimator` using the `attach` method.

In [8]:
from sagemaker.huggingface import HuggingFace

# Check if the huggingface_estimator is defined, if not we restore the training job to our estimator variable
try:
    model_dir = huggingface_estimator.model_data
except:
    # Set the training job you want to attach to the estimator object
    # Use this option if the training job was not trained in this execution
    my_training_job_name = 'ruperta-sentiment-analysis-beto-p2-2021-12-24-11-53-44'

    # Attach the estimator to the selected training job
    huggingface_estimator = HuggingFace.attach(my_training_job_name)
    print('Restored Huggingface estimator')
    model_dir= huggingface_estimator.model_data


2021-12-24 22:35:02 Starting - Preparing the instances for training
2021-12-24 22:35:02 Downloading - Downloading input data
2021-12-24 22:35:02 Training - Training image download completed. Training in progress.
2021-12-24 22:35:02 Uploading - Uploading generated training model
2021-12-24 22:35:02 Completed - Training job completed
Restored Huggingface estimator


In [19]:
# Check if the huggingface_estimator is defined, if not we restore the training job to our estimator variable
try:
    print('Input data for testing: ', test_data_input)
except:
    # Set the training job you want to attach to the estimator object
    # Use this option if the training job was not trained in this execution
    # Save the test dataset to jsonl file
    test_filename = 'test_data.jsonl'
    test_data_input = test_data_uri+'/'+test_filename


Input data for testing:  s3://edumunozsala-ml-sagemaker/ruperta-sentiment/test//home/ec2-user/SageMaker/ruperta_sentiment_analysis/data/test_data.jsonl


Create a Batch Transform job to inference the test dataset

In [24]:
# create Transformer to run our batch job using the estimator
batch_job = huggingface_estimator.transformer(
    instance_count=1,
    instance_type='ml.m5.xlarge',
    output_path=test_data_uri, # we are using the same s3 path to save the output with the input
    strategy='SingleRecord')

# starts batch transform job and uses s3 data as input
batch_job.transform(
    data=test_data_input,
    content_type='application/json',    
    split_type='Line')

..................................2021-12-25T11:52:47.836:[sagemaker logs]: MaxConcurrentTransforms=1, MaxPayloadInMB=6, BatchStrategy=SINGLE_RECORD
2021-12-25 11:52:47,206 [INFO ] main com.amazonaws.ml.mms.ModelServer - 
MMS Home: /opt/conda/lib/python3.6/site-packages
2021-12-25 11:52:47,206 [INFO ] main com.amazonaws.ml.mms.ModelServer - 
MMS Home: /opt/conda/lib/python3.6/site-packages
Current directory: /
Temp directory: /home/model-server/tmp
Number of GPUs: 0
Number of CPUs: 4
Max heap size: 2622 M
Python executable: /opt/conda/bin/python3.6
Config file: /etc/sagemaker-mms.properties
Inference address: http://0.0.0.0:8080
Management address: http://0.0.0.0:8080
Model Store: /.sagemaker/mms/models
Initial Models: ALL
Log dir: /logs
Metrics dir: /logs
Netty threads: 0
Netty client threads: 0
Default workers per model: 4
Blacklist Regex: N/A
Maximum Response Size: 6553500
Maximum Request Size: 6553500
Preload model: false
Prefer direct buffer: false
2021-12-25 11:52:47,280 [WARN ] 

2021-12-25 11:53:07,735 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.025987625122070312 ms
2021-12-25 11:53:07,735 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433187734.6343 ms
2021-12-25 11:53:07,735 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 156
2021-12-25 11:53:07,735 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 156
2021-12-25 11:53:07,735 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.0762939453125 ms
2021-12-25 11:53:07,735 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.025987625122070312 ms
2021-12-25 11:53:07,735 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433187734.6343 ms
2021-12-25 11:53:07,735 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 156
20

2021-12-25 11:53:17,323 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 150
2021-12-25 11:53:17,323 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.07319450378417969 ms
2021-12-25 11:53:17,481 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.024318695068359375 ms
2021-12-25 11:53:17,482 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433197481.3792 ms
2021-12-25 11:53:17,482 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.0743865966796875 ms
2021-12-25 11:53:17,484 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 158
2021-12-25 11:53:17,484 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 159
2021-12-25 11:53:17,640 [INFO ] W-model-1-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.0314712524

2021-12-25 11:53:27,866 [INFO ] W-model-2-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.023603439331054688 ms
2021-12-25 11:53:27,867 [INFO ] W-model-2-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433207866.6614 ms
2021-12-25 11:53:27,867 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 158
2021-12-25 11:53:27,867 [INFO ] W-model-2-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.07319450378417969 ms
2021-12-25 11:53:27,867 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 158
2021-12-25 11:53:28,044 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.025987625122070312 ms
2021-12-25 11:53:28,044 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433208043.9583 ms
2021-12-25 11:53:28,044 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 17

2021-12-25 11:53:37,791 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.023603439331054688 ms
2021-12-25 11:53:37,791 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433217790.9124 ms
2021-12-25 11:53:37,791 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 175
2021-12-25 11:53:37,791 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.0743865966796875 ms
2021-12-25 11:53:37,791 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 176
2021-12-25 11:53:37,791 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.023603439331054688 ms
2021-12-25 11:53:37,791 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433217790.9124 ms
2021-12-25 11:53:37,791 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 175

...

2021-12-25 12:02:38,476 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.02384185791015625 ms
2021-12-25 12:02:38,476 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.02384185791015625 ms
2021-12-25 12:02:38,476 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433758476.3865 ms
2021-12-25 12:02:38,476 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.07367134094238281 ms
2021-12-25 12:02:38,476 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 156
2021-12-25 12:02:38,476 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 156
2021-12-25 12:02:38,636 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.025272369384765625 ms
2021-12-25 12:02:38,636 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 

2021-12-25 12:02:47,879 [INFO ] W-model-2-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.025510787963867188 ms
2021-12-25 12:02:47,879 [INFO ] W-model-2-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433767879.343 ms
2021-12-25 12:02:47,879 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 144
2021-12-25 12:02:47,879 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 144
2021-12-25 12:02:47,880 [INFO ] W-model-2-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.07605552673339844 ms
2021-12-25 12:02:48,045 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.024557113647460938 ms
2021-12-25 12:02:48,045 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433768045.0674 ms
2021-12-25 12:02:48,045 [INFO ] W-model-4-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 

2021-12-25 12:02:56,570 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.02384185791015625 ms
2021-12-25 12:02:56,570 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433776570.1636 ms
2021-12-25 12:02:56,570 [INFO ] W-model-3-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.07367134094238281 ms
2021-12-25 12:02:56,570 [INFO ] W-9000-model com.amazonaws.ml.mms.wlm.WorkerThread - Backend response time: 154
2021-12-25 12:02:56,570 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 200 154
2021-12-25 12:02:56,791 [INFO ] W-model-1-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Preprocess time - 0.0209808349609375 ms
2021-12-25 12:02:56,791 [INFO ] W-model-1-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Predict time - 1640433776790.9214 ms
2021-12-25 12:02:56,791 [INFO ] W-model-1-stdout com.amazonaws.ml.mms.wlm.WorkerLifeCycle - Postprocess time - 0.

2021-12-25 12:03:07,339 [INFO ] W-9000-model ACCESS_LOG - /169.254.255.130:50374 "POST /invocations HTTP/1.1" 400 3

2021-12-25T12:03:07.345:[sagemaker logs]: edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out: ClientError: 400
2021-12-25T12:03:07.345:[sagemaker logs]: edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out: 
2021-12-25T12:03:07.345:[sagemaker logs]: edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out: Message:
2021-12-25T12:03:07.345:[sagemaker logs]: edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out: {
2021-12-25T12:03:07.349:[sagemaker logs]: edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out:   "code": 400,
2021-12-25T12:03:07.350:[sagemaker logs]: edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out:   "type": "InternalServerException",
2021-12-25T12:03:07.350:[sagemaker logs]: edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out:   "message": "Extr

UnexpectedStatusException: Error for Transform job ruperta-sentiment-analysis-beto-p2-2021-2021-12-25-11-47-25-502: Failed. Reason: ClientError: See job logs for more information

In the output path of our inference job we can find a file with the predictions for our test dataset and we saved the true labels in the data directory so we can calculate the performance of the model.

In [25]:
!pip install jsonlines

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com


Read the labels of our test dataset that we saved previously

In [33]:
import jsonlines

# Define the test labels json lines file
test_labels_filename = os.path.abspath(os.path.join(data_folder_name, 'test_labels.jsonl'))
# Iterate over the json lines to extract the content
with jsonlines.open(test_labels_filename, 'r') as jsonl_f:
     labels = [obj for obj in jsonl_f]
        
print(len(labels))
print(labels[0:10])

3750
[{'labels': 0}, {'labels': 0}, {'labels': 1}, {'labels': 0}, {'labels': 1}, {'labels': 0}, {'labels': 1}, {'labels': 1}, {'labels': 0}, {'labels': 0}]


Read the predictions generated by our model in the inference job

In [29]:
from sagemaker.s3 import S3Downloader
#Set the S3 file to download
try:
    test_data_input = 's3://edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out'
except:
    test_data_input = 's3://'+sagemaker_session_bucket+'/'+test_folder+'/test_data.jsonl.out'

print(test_data_input)

# Define the folder where the labels
#mymodel_name='RuPERTa_base_sentiment_analysis_es'
#local_path = mymodel_name

# download the output of the inference job from S3
S3Downloader.download(
    s3_uri=test_data_input, # s3 uri where the predicted labels are located
    local_path=data_folder_name, # local path where it will be saved
    sagemaker_session=sess # sagemaker session used for training the model
)

s3://edumunozsala-ml-sagemaker/ruperta-sentiment/test/test_data.jsonl.out


In [34]:
from ast import literal_eval

# Define the test labels json lines file
pred_labels_filename = os.path.abspath(os.path.join(data_folder_name, 'test_data.jsonl.out'))
# Iterate over the json lines to extract the content
batch_transform_result = []

with open(pred_labels_filename) as f:
    for line in f:
        # converts jsonline array to normal array
        line = "[" + line.replace("[","").replace("]",",") + "]"
        batch_transform_result = literal_eval(line) 
        
# print results 
print(batch_transform_result[:3])
print(len(batch_transform_result))

[{'label': 'Negativo', 'score': 0.5882746577262878}, {'label': 'Positivo', 'score': 0.7747754454612732}, {'label': 'Positivo', 'score': 0.9961003661155701}]
3750


Once the files are read, we can calculate the metrics using the sklearn package

In [35]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

#Extract the tru labels
preds = [1 if v['label']=='Positivo' else 0 for v in batch_transform_result]
labels = [l['labels'] for l in labels]
# Check the length of the results
print(len(preds), len(labels))

test_precision, test_recall, test_f1, _ = precision_recall_fscore_support(labels, preds, average="binary")
test_acc = accuracy_score(labels, preds)

print('Precision: ',test_precision,' Recall: ',test_recall,' F1 Score:', test_f1)
print('Accuracy: ',test_acc)

3750 3750
Precision:  0.8116615067079463  Recall:  0.8158713692946058  F1 Score: 0.8137609932747025
Accuracy:  0.808


# Upload the model to Hugginface Hub

In this last section, once our model is trained and evaluated and if the performance is good enough, we can upload it to the Huggingface Hub to share it with other ML practicioners. 

Code extracted from a post in the huggingface blog: https://huggingface.co/blog/sagemaker-distributed-training-seq2seq

First install git-lfs for model upload.

In [6]:
!curl -s https://packagecloud.io/install/repositories/github/git-lfs/script.rpm.sh | sudo bash
!sudo yum install git-lfs -y
!git lfs install

Detected operating system as amzn/2.
Checking for curl...
Detected curl...
done.
Installing pygpgme to verify GPG signatures...
Loaded plugins: dkms-build-requires, extras_suggestions, langpacks, priorities,
              : update-motd, versionlock
amzn2-core                                               | 3.7 kB     00:00     
github_git-lfs-source/signature                          |  833 B     00:00     
Retrieving key from https://packagecloud.io/github/git-lfs/gpgkey
Importing GPG key 0xDC282033:
 Userid     : "https://packagecloud.io/github/git-lfs (https://packagecloud.io/docs#gpg_signing) <support@packagecloud.io>"
 Fingerprint: 6d39 8dbd 30dd 7894 1e2c 4797 fe2a 5f8b dc28 2033
 From       : https://packagecloud.io/github/git-lfs/gpgkey
github_git-lfs-source/signature                          | 1.8 kB     00:00 !!! 
neuron                                                   | 2.9 kB     00:00     
github_git-lfs-source/primary                              | 4.8 kB   00:00     
gi

Next, we are going to upload our trained model to huggingface.co. To upload a model you need to create an account in huggingface.com.

First, we create a local path to store the model repository

In [8]:
import os
import tarfile
from sagemaker.s3 import S3Downloader

# Define the my final model name
mymodel_name='RuPERTa_base_sentiment_analysis_es'
local_path = mymodel_name
# Create a local path for the model repository
os.makedirs(local_path, exist_ok = True)

We log in to Huggingface and get an access token to create a temporary local repository cloned from the Huggingface model hub, if it exists

In [12]:
from getpass import getpass

hf_username = "edumunozsala" # your username on huggingface.co
hf_email = "edumunozsala@gmail.com" # email used for commit
repository_name = mymodel_name
password = getpass("Enter your password:") # creates a prompt for entering password

Enter your password:········


In [10]:
repository_name,  local_path

('RuPERTa_base_sentiment_analysis_es', 'RuPERTa_base_sentiment_analysis_es')

After we have our unzipped model and model card located in my_bart_model we can use the either huggingface_hub SDK to create a repository and upload it to huggingface.co – or just to https://huggingface.co/new an create a new repository and upload it.

**Important: repository_name dir must not exist**

In [14]:
from huggingface_hub import HfApi, Repository

# get hf token
token = HfApi().login(username=hf_username, password=password)

# create repository
repo_url = HfApi().create_repo(token=token, name=repository_name, exist_ok=True)

# create a Repository instance
model_repo = Repository(use_auth_token=token,
                        clone_from=repo_url,
                        local_dir=local_path,
                        git_user=hf_username,
                        git_email=hf_email)

ERROR:root:HfApi.login: This method is deprecated in favor of `set_access_token`.
Cloning https://huggingface.co/edumunozsala/RuPERTa_base_sentiment_analysis_es into local empty directory.


We can download our model from Amazon S3 and unzip it using the following snippet. Then, our repository dir is updated with lastest trained model saved in S3.
First, we check if the estimator is defined (the training_job was launched in this session) if not we restore the training job to our estimator.

In [18]:
from sagemaker.huggingface import HuggingFace

#Set the S3 URI with the model data
# Check if the huggingface_estimator is defined, if not we restore the training job to our estimator variable
try:
    model_dir = huggingface_estimator.model_data
except:
    # Set the training job you want to attach to the estimator object
    # Use this option if the training job was not trained in this execution
    my_training_job_name = 'ruperta-sentiment-analysis-full-p2-2021-12-06-20-32-27'

    # Attach the estimator to the selected training job
    huggingface_estimator = HuggingFace.attach(my_training_job_name)
    print('Restored Huggingface estimator')
    model_dir= huggingface_estimator.model_data


2021-12-07 04:46:04 Starting - Preparing the instances for training
2021-12-07 04:46:04 Downloading - Downloading input data
2021-12-07 04:46:04 Training - Training image download completed. Training in progress.
2021-12-07 04:46:04 Uploading - Uploading generated training model
2021-12-07 04:46:04 Completed - Training job completed
Restored Huggingface estimator


Download our previously trained job to the local git repository

In [20]:
# download model from S3
S3Downloader.download(
    s3_uri=model_dir, # s3 uri where the trained model is located
    local_path=local_path, # local path where *.tar.gz will be saved
    sagemaker_session=sess # sagemaker session used for training the model
)

# unzip model
tar = tarfile.open(f"{local_path}/model.tar.gz", "r:gz")
tar.extractall(path=local_path)
tar.close()
os.remove(f"{local_path}/model.tar.gz")

Extract the evaluation results from the file output.tar.gz

In [21]:
# unzip evaluation results
tar = tarfile.open(f"{local_path}/output.tar.gz", "r:gz")
tar.extractall(path=local_path)
tar.close()
os.remove(f"{local_path}/output.tar.gz")

After we extract all the files we want to include in out model, we are going to create a README.md. Additionally to the automated generation of the results table we add the metrics manually to the metadata of our model card under model-index.

Read the evaluation results and the README file to string variables and build a simple README.md file for our model. Later you must edit the README file manually to complete the information and improve the composition.

In [32]:
import json
# Read the evaluation results
with open(f"{local_path}/eval_results.txt") as f:
    eval_results = f.read()
    
# Read the README file
with open(f"{local_path}/README.txt") as f:
    readme = f.read()  
    
# Generate model card (todo: add more data from Trainer)
model_card = readme.format(
    model_name=mymodel_name,
    hyperparameters=json.dumps(huggingface_estimator.hyperparameters(), indent=4, sort_keys=True),
    eval_results=eval_results
)

with open(f"{local_path}/README.md", "w") as f:
    f.write(model_card)

Finally we push the model repository to the hub, we highly recomend you to clean the directory to upload only the neccessary files.

In [33]:
# push model to the hub
model_repo.push_to_hub()

Upload file checkpoint-5316/optimizer.pt:   0%|          | 32.0k/961M [00:00<?, ?B/s]

Upload file checkpoint-5316/scaler.pt: 100%|##########| 559/559 [00:00<?, ?B/s]

Upload file pytorch_model.bin:   0%|          | 32.0k/481M [00:00<?, ?B/s]

Upload file checkpoint-5316/pytorch_model.bin:   0%|          | 32.0k/481M [00:00<?, ?B/s]

Upload file checkpoint-5316/rng_state.pth: 100%|##########| 14.3k/14.3k [00:00<?, ?B/s]

Upload file checkpoint-5316/training_args.bin: 100%|##########| 2.36k/2.36k [00:00<?, ?B/s]

Upload file checkpoint-5316/scheduler.pt: 100%|##########| 623/623 [00:00<?, ?B/s]

remote: ----------------------------------------------------------        
remote: Your push was accepted, but with warnings:        
remote: - warning : empty or missing yaml metadata in card (edumunozsala/RuPERTa_base_sentiment_analysis_es)        
remote: help: please find help at https://huggingface.co/docs/hub/model-repos        
remote: ----------------------------------------------------------        
remote: Please find the documentation at:        
remote: https://huggingface.co/docs/hub/model-repos(B        
remote: ----------------------------------------------------------        
To https://huggingface.co/edumunozsala/RuPERTa_base_sentiment_analysis_es
   0d59578..94189dd  main -> main

remote: Your push was accepted, but with warnings:        
remote: - warning : empty or missing yaml metadata in card (edumunozsala/RuPERTa_base_sentiment_analysis_es)        
remote: help: please find help at https://huggingface.co/docs/hub/model-repos        
remote: ---------------------

'https://huggingface.co/edumunozsala/RuPERTa_base_sentiment_analysis_es/commit/94189dd6870cf37d10be4299475071c48eb5b055'

After we uploaded our model we can access it at https://huggingface.co/{hf_username}/{repository_name}:

In [ ]:
print(f"https://huggingface.co/{hf_username}/{repository_name}")

## References

- Some sections of this notebook has been inspired by the tutorial on Huggingface doc:
https://github.com/huggingface/notebooks/blob/master/sagemaker/01_getting_started_pytorch/sagemaker-notebook.ipynb

- Apply Batch Transform inference:
https://github.com/huggingface/notebooks/blob/master/sagemaker/12_batch_transform_inference/sagemaker-notebook.ipynb

- Hot to upload the model to the Hub
https://huggingface.co/blog/sagemaker-distributed-training-seq2seq
